# Vertex AI Custom Training Job - Custom Training Job 구성 및 실행

이 노트북은 Vertex AI Custom Training Job을 이용한 모델 학습 과정을 단계별로 설명합니다.

In [ ]:
# 작업 1 - 기본 설정

import os
from google.cloud import aiplatform, storage
import subprocess

# 필요한 패키지 설치
subprocess.run(["pip", "install", "torch", "torchvision", "google-cloud-aiplatform", "google-cloud-storage", "pyyaml"])

import torch
import torchvision
import zipfile

# GCP 프로젝트 설정
PROJECT_ID = "prd-center-gcp"  # GCP 프로젝트 ID
REGION = "us-central1"  # 리전 설정
BUCKET_NAME = "test-coco-dataset-bucket"  # GCS 버킷 이름

# Vertex AI 초기화
aiplatform.init(project=PROJECT_ID, location=REGION)

In [ ]:
# 작업 2 - COCO 데이터셋 및 기계 학습 환경 다운로드

# COCO 데이터셋 및 학습 코드 다운로드
!wget https://github.com/ultralytics/assets/releases/download/v0.0.0/coco128.zip
!wget https://raw.githubusercontent.com/ultralytics/yolov5/master/data/coco128.yaml
!wget https://raw.githubusercontent.com/ultralytics/yolov5/master/train.py

# 데이터 압축 해제
import zipfile
with zipfile.ZipFile("coco128.zip", "r") as zip_ref:
    zip_ref.extractall("coco128")

In [ ]:
# 작업 3 - GCS 버킷 생성 및 업로드

# GCS 버킷 생성
storage_client = storage.Client()
bucket = storage_client.create_bucket(BUCKET_NAME, location=REGION)

# GCS 버킷에 업로드
!gsutil -m cp -r coco128 gs://{BUCKET_NAME}/coco/
!gsutil -m cp -r coco128.yaml gs://{BUCKET_NAME}/coco/
!gsutil -m cp -r train.py gs://{BUCKET_NAME}/coco/

In [ ]:
# 작업 4 - Custom Training Job 실행

!gcloud ai custom-jobs create \
  --region=us-central1 \
  --display-name=yolo-training-job \
  --worker-pool-spec=machine-type=n1-standard-8,replica-count=1,accelerator-type=NVIDIA_TESLA_T4,accelerator-count=1,container-image-uri=gcr.io/deeplearning-platform-release/pytorch-gpu.1-12:latest \
  --command=bash \
  --args="-c" \
  --args="\
  git clone https://github.com/ultralytics/yolov5.git && \
  gsutil -m cp -r gs://{BUCKET_NAME}/coco/coco128/coco128 yolov5/ && \
  gsutil -m cp -r gs://{BUCKET_NAME}/coco/coco128.yaml yolov5/ && \
  gsutil -m cp -r gs://{BUCKET_NAME}/coco/train.py yolov5/ && \
  cd yolov5 && \
  pip install --upgrade pip && \
  pip install -r requirements.txt && \
  python train.py --data=coco128.yaml --epochs=10 --batch-size=16 --img-size=640 && \
  gsutil -m cp -r runs/train/* gs://{BUCKET_NAME}/coco/models/"
